# PyROOT
<img src="https://root.cern/img/logos/ROOT_Logo/misc/logo_full-plus-text-hor.png" width="350" />
<img src="https://www.python.org/static/community_logos/python-logo-generic.svg" width="350" style='margin-left: 10px' />

In [ ]:
import ROOT

Possibility to define `C++` namespaces

In [ ]:
ROOT.gInterpreter.Declare('''
    using namespace ROOT::Math;
    using namespace ROOT::VecOps;

    using P3 = XYZVector;
    using P4E = PxPyPzEVector;
    using P4M = PxPyPzMVector;
''')

Create `RDataFrame` with name of the tree and path to the `ROOT` files

In [ ]:
df = ROOT.RDataFrame('tree_name', 'path/to/root_files/*.root')

Print all available columns

In [ ]:
print(*df.GetColumnNames(), sep=', ')

## Define four-vectors and other derived quantities

Apply cut on the $\chi^2$ of the four-contraint kinematic fit

In [ ]:
df_fit = df.Filter('dblKinFit4CChiSq > 0 && dblKinFit4CChiSq < 100', 'Kin Fit')

*Final state: $J/\psi \pi^+ \pi^-$ ($J/\psi \to e^+ e^- / \mu^+ \mu^-$)*

Define 4-momenta for the particles

In [ ]:
df_fit_2 = df_fit \
    .Define('p4PiP', 'P4E(dblKinFit4CMomentaPx[0], dblKinFit4CMomentaPy[0], dblKinFit4CMomentaPz[0], dblKinFit4CMomentaE[0])') \
    .Define('p4PiM', 'P4E(dblKinFit4CMomentaPx[1], dblKinFit4CMomentaPy[1], dblKinFit4CMomentaPz[1], dblKinFit4CMomentaE[1])') \
    .Define('p4LepP', 'P4E(dblKinFit4CMomentaPx[2], dblKinFit4CMomentaPy[2], dblKinFit4CMomentaPz[2], dblKinFit4CMomentaE[2])') \
    .Define('p4LepM', 'P4E(dblKinFit4CMomentaPx[3], dblKinFit4CMomentaPy[3], dblKinFit4CMomentaPz[3], dblKinFit4CMomentaE[3])')

Define derived quantities like combined vectors, invariant masses, or relative angles

In [ ]:
df_fit_3 = df_fit_2 \
    .Define('p4Jpsi', 'p4LepP + p4LepM') \
    .Define('mJpsi', 'p4Jpsi.M()') \
    .Define('mJpsiPiP', '(p4Jpsi + p4PiP).M()') \
    .Define('mJpsiPiM', '(p4Jpsi + p4PiM).M()') \
    .Define('mJpsiPiMax', 'mJpsiPiP > mJpsiPiM ? mJpsiPiP : mJpsiPiM') \
    .Define('mPiPi', '(p4PiP + p4PiM).M()') \
    .Define('cosThetaPiPi', 'VectorUtil::CosTheta(p4PiP, p4PiM)') \
    .Define('Dalitz_x', '(p4PiP + p4Jpsi).M2()') \
    .Define('Dalitz_y', '(p4PiP + p4PiM).M2()')

Print column types for verification

In [ ]:
print(df_fit_3.GetColumnType('p4PiP'), df_fit_3.GetColumnType('p4Jpsi'), df_fit_3.GetColumnType('mJpsi'), sep='\n')

Define cut to suppress background

In [ ]:
df_angle = df_fit_3.Filter('abs(cosThetaPiPi) < 0.9', 'Pion Angle')

## Fit $J/\psi$ Peak

Define histograms for each leptonic decay channel

In [ ]:
h = {}
h['ee'] = df_angle \
    .Filter('intNumberElectrons == 2') \
    .Histo1D(ROOT.RDF.TH1DModel('hJpsiMass_ee', ';m_{e^{+}e^{-}} / GeV;Events / 1 MeV', 5000, 0., 5.), 'mJpsi')
h['mumu'] = df_angle \
    .Filter('intNumberMuons == 2') \
    .Histo1D(ROOT.RDF.TH1DModel('hJpsiMass_mumu', ';m_{#mu^{+}#mu^{-}} / GeV;Events / 1 MeV', 5000, 0., 5.), 'mJpsi')
h['ll'] = df_angle \
    .Histo1D(ROOT.RDF.TH1DModel('hJpsiMass_ll', ';m_{l^{+}l^{-}} / GeV;Events / 1 MeV', 5000, 0., 5.), 'mJpsi')

bin_width = 0.001

Define fit functions for Gaussian and Voigt for each channel

In [ ]:
f_gaussian = {}
f_voigt = {}

for key in ['ee', 'mumu', 'll']:

    f_gaussian[key] = ROOT.TF1(f'f_gaussian_{key}', '[0]*gaussian_pdf(x,[2],[1])+[3]+[4]*x', 3.0, 3.2)
    f_gaussian[key].SetParameters(1, 3.1, 0.005, 0, 0)
    f_gaussian[key].SetParNames('A', '#mu', '#sigma', 'a', 'b')
    f_gaussian[key].SetParLimits(0, 0.001, 1000)
    f_gaussian[key].SetParLimits(1, 3.0, 3.2)
    f_gaussian[key].SetParLimits(2, 0.0001, 0.1)
    f_gaussian[key].SetLineColor(ROOT.kRed)
    f_gaussian[key].SetNpx(10000)


    f_voigt[key] = ROOT.TF1(f'f_voigt_{key}', '[0]*TMath::Voigt(x-[1],[2],[3])+[4]+[5]*x', 3.0, 3.2)
    f_voigt[key].SetParameters(1, 3.1, 0.005, 0.001, 0, 0)
    f_voigt[key].SetParNames('A', '#mu', '#sigma_G', '#sigma_BW', 'a', 'b')
    f_voigt[key].SetParLimits(0, 0.001, 1000)
    f_voigt[key].SetParLimits(1, 3.0, 3.2)
    f_voigt[key].SetParLimits(2, 0.0001, 0.1)
    f_voigt[key].SetParLimits(3, 0.0001, 0.1)
    f_voigt[key].SetLineColor(ROOT.kGreen)
    f_voigt[key].SetNpx(10000)

Fit histograms

In [ ]:
for i, key in enumerate(['ee', 'mumu', 'll']):

    print(key)

    h[key].Fit(f_gaussian[key], '0', '', 3.0, 3.2)
    h[key].Fit(f_voigt[key], '0', '', 3.0, 3.2)

    print(f'Gaussian chi^2/ndf: {f_gaussian[key].GetChisquare()/f_gaussian[key].GetNDF():.3f}')
    print(f'Voigt    chi^2/ndf: {f_voigt[key].GetChisquare()/f_voigt[key].GetNDF():.3f}')
    print(f'Gaussian Integral : {f_gaussian[key].GetParameter(0)/bin_width:7.3f} +- {f_gaussian[key].GetParError(0)/bin_width:6.3f}')
    print(f'Voigt    Integral : {f_voigt[key].GetParameter(0)/bin_width:7.3f} +- {f_voigt[key].GetParError(0)/bin_width:6.3f}')

Plot fit results for each channel

In [ ]:
c = ROOT.TCanvas('c', '', 1200, 500)
c.Divide(3, 1)

for i, key in enumerate(['ee', 'mumu', 'll']):

    c.cd(i+1)

    h[key].SetTitle(h[key].GetXaxis().GetTitle())
    h[key].Draw('E1')
    h[key].GetXaxis().SetRangeUser(3.0, 3.2)

    f_gaussian[key].Draw('same')
    f_voigt[key].Draw('same')

c.Draw()

Evaluate position and width of the peak

In [ ]:
fit_results = f_voigt['ll']

peak = (
    fit_results.GetParameter(1),
    fit_results.GetParError(1)
)
width_linear = (
    fit_results.GetParameter(2) + fit_results.GetParameter(3),
    fit_results.GetParError(2) + fit_results.GetParError(3)
)
width_quadratic = (
    (fit_results.GetParameter(2)**2 + fit_results.GetParameter(3)**2)**(1/2),
    ((fit_results.GetParameter(2) * fit_results.GetParError(2))**2 + (fit_results.GetParameter(3) * fit_results.GetParError(3))**2)**(1/2)/
        (fit_results.GetParameter(2)**2 + fit_results.GetParameter(3)**2)**(1/2)
)

print(f"Peak Position       : ({peak[0]*1000:.2f} +- {peak[1]*1000:.2f}) MeV")
print(f"Peak Width Linear   : ({width_linear[0]*1000:.3f} +- {width_linear[1]*1000:.3f}) MeV")
print(f"Peak Width Quadratic: ({width_quadratic[0]*1000:.3f} +- {width_quadratic[1]*1000:.3f}) MeV")

## Define Sideband Regions

In [ ]:
peak_pos = peak[0]
sideband_width = 2 * 3 * width_linear[0] # +- 3 sigma
sideband_offset = 2 * 3 * width_linear[0]

Apply filters to define the signal and sideband regions

In [ ]:
df_sig = df_angle.Filter(f'abs(mJpsi - {peak_pos}) <= {sideband_width} / 2', 'Signal')
df_sb_l = df_angle.Filter(f'abs(mJpsi - {peak_pos} + {sideband_offset}) <= {sideband_width} / 2', 'SB Left')
df_sb_r = df_angle.Filter(f'abs(mJpsi - {peak_pos} - {sideband_offset}) <= {sideband_width} / 2', 'SB Right')

Create histogram ($m_{\pi^+\pi^-}$) in each region

In [ ]:
h_pipi_sig = df_sig.Histo1D(ROOT.RDF.TH1DModel('hPiPiMass', ';m_{#pi^{+}#pi^{-}} / GeV;Events / 10 MeV', 500, 0., 5.), 'mPiPi')
h_pipi_sb_l = df_sb_l.Histo1D(ROOT.RDF.TH1DModel('hPiPiMass', ';m_{#pi^{+}#pi^{-}} / GeV;Events / 10 MeV', 500, 0., 5.), 'mPiPi')
h_pipi_sb_r = df_sb_r.Histo1D(ROOT.RDF.TH1DModel('hPiPiMass', ';m_{#pi^{+}#pi^{-}} / GeV;Events / 10 MeV', 500, 0., 5.), 'mPiPi')

Subtract sidebands from signal

In [ ]:
h_pipi_sig

In [ ]:
h_pipi_sub = h_pipi_sig.Clone()
h_pipi_sub.Add(h_pipi_sb_l.GetValue(), -0.5)
h_pipi_sub.Add(h_pipi_sb_r.GetValue(), -0.5)

Set line colors

In [ ]:
h_pipi_sig.SetLineColor(ROOT.kRed)
h_pipi_sb_l.SetLineColor(ROOT.kGreen)
h_pipi_sb_r.SetLineColor(ROOT.kOrange)
h_pipi_sub.SetLineColor(ROOT.kBlue)

Plot data

In [ ]:
c = ROOT.TCanvas()
h_pipi_sig.Draw()
h_pipi_sb_l.Draw('SAME')
h_pipi_sb_r.Draw('SAME')
h_pipi_sub.Draw('SAME')
h_pipi_sig.GetXaxis().SetRangeUser(0.2, 1.4)
h_pipi_sig.GetYaxis().SetRangeUser(-10, 90)
c.Draw()

## Dalitz Plot

Define histogram ($m^2_{\pi^+ J/\psi}$, $m^2_{\pi^+ \pi^-}$) in each region

In [ ]:
h_Dalitz_sig = df_sig.Histo2D(
    ROOT.RDF.TH2DModel('h_Dalitz_sig', ';m_{#pi^{+}J/#psi}^{2} / GeV^{2};m_{#pi^{+}#pi^{-}}^{2} / GeV^{2};Events / (0.1 GeV^{2} * 0.05 GeV^{2})', 200, 0, 20, 400, 0, 20),
    'Dalitz_x', 'Dalitz_y')
h_Dalitz_sb_l = df_sb_l.Histo2D(
    ROOT.RDF.TH2DModel('h_Dalitz_sb_l', ';m_{#pi^{+}J/#psi}^{2} / GeV^{2};m_{#pi^{+}#pi^{-}}^{2} / GeV^{2};Events / (0.1 GeV^{2} * 0.05 GeV^{2})', 200, 0, 20, 400, 0, 20),
    'Dalitz_x', 'Dalitz_y')
h_Dalitz_sb_r = df_sb_r.Histo2D(
    ROOT.RDF.TH2DModel('h_Dalitz_sb_r', ';m_{#pi^{+}J/#psi}^{2} / GeV^{2};m_{#pi^{+}#pi^{-}}^{2} / GeV^{2};Events / (0.1 GeV^{2} * 0.05 GeV^{2})', 200, 0, 20, 400, 0, 20),
    'Dalitz_x', 'Dalitz_y')

Subtract sidebands from signal

In [ ]:
h_Dalitz_sub = h_Dalitz_sig.Clone('h_Dalitz_sub')
h_Dalitz_sub.Add(h_Dalitz_sb_l.GetValue(), -0.5)
h_Dalitz_sub.Add(h_Dalitz_sb_r.GetValue(), -0.5)

Plot data

In [ ]:
c2 = ROOT.TCanvas()
h_Dalitz_sub.Draw('COLZ')
h_Dalitz_sub.GetXaxis().SetRangeUser(10, 17)
h_Dalitz_sub.GetYaxis().SetRangeUser(0, 1.5)
c2.Draw()

Define function to draw kinematical constraints of final state $J/\psi \, \pi^+ \, \pi^-$

Needs center-of-mass energy $\sqrt{s}$ and restmasses of all particles

<img src='https://github.com/scikit-hep/particle/raw/master/docs/ParticleLogo300.png' width='150px' />

Use `particle` package to obtain rest masses (in MeV) from PDG

In [ ]:
from particle import literals as lp

m1 = lp.Jpsi_1S.mass / 1000
m2 = lp.pi_plus.mass / 1000
m3 = lp.pi_minus.mass / 1000

Read center-of-mass energy from data frame

In [ ]:
sqrt_s = df.AsNumpy(['dblCmsEnergy'])['dblCmsEnergy'][0] # get CMS energy from first event

Define kinematical functions in Python

In [ ]:
def lambda_f(x: float, y: float, z: float) -> float:
    return x**2 + y**2 + z**2 - 2.0 * (x * y + x * z + y * z)

def s1_constr(s3: float, s: float, m1_2: float, m2_2: float, m3_2: float, sign: int) -> float:
    return m3_2 + m2_2 + 0.5 / s3 * ((s - s3 - m3_2) * (s3 - m1_2 + m2_2) + sign * ROOT.sqrt(lambda_f(s3, s, m3_2) * lambda_f(s3, m1_2, m2_2)))

Define `ROOT.TF1` object to draw contraints

In [ ]:
s3_min = (m1 + m2)**2
s3_max = (sqrt_s - m3)**2

def f1(x, p):
    return s1_constr(x[0], p[0], p[1], p[2], p[3], p[4])

f = ROOT.TF1('f', f1, s3_min, s3_max, 5)
f.SetParameters(sqrt_s**2, m1**2, m2**2, m3**2, 1)
f.SetNpx(100000)

Plot data and constraints

In [ ]:
c3 = ROOT.TCanvas()
h_Dalitz_sub.Draw('COLZ')
h_Dalitz_sub.GetXaxis().SetRangeUser(10, 17)
h_Dalitz_sub.GetYaxis().SetRangeUser(0, 1.5)
f.SetParameter(4, 1)
f.DrawCopy('same')
f.SetParameter(4, -1)
f.DrawCopy('same')
c3.Draw()

Save canvas as PDF

In [ ]:
c3.SaveAs('Dalitz.pdf')

## Cut Report

### Signal Region

In [ ]:
r = df_sig.Report()
r.Print()

### Left Sideband Region

In [ ]:
r = df_sb_l.Report()
r.Print()

### Right Sideband Region

In [ ]:
r = df_sb_r.Report()
r.Print()

Print graph of data frame

In [ ]:
ROOT.RDF.SaveGraph(df, 'df.dot')
!dot -Tpng df.dot > df.png

<img src='df.png' width='800px' />

## More 'advanced' processing

Use `C++` code to perform defitions over arrays

In [ ]:
df_2 = df \
    .Define('pTracks', '''
        RVec<P3> pTracks(intNumberGoodChargedTracks);
        for (int i = 0; i < intNumberGoodChargedTracks; i++) {
            pTracks[i] = P3(dblTracksPx[i], dblTracksPy[i], dblTracksPz[i]);
        }
        return pTracks;
    ''') \
    .Define('pMag', '''
        RVec<double> pMag(pTracks.size());
        for (int i = 0; i < intNumberGoodChargedTracks; i++) {
            pMag[i] = pTracks[i].R();
        }
        return pMag;
    ''')

Check type of new defined columns

In [ ]:
print(df_2.GetColumnType('pTracks'), df_2.GetColumnType('pMag'), sep='\n')